## Project Overview 

This project aims to create two machine learning classifiers that predicts the genre of a song after inputting lyrics as well as by using the audio qualities. This project will use datasets from Kaggle and data scraped from genius.com.

Problem statement: Can we build a model that uses various lyrics and audio attributes to accurately predict the genre of a song?

Prompt: You are working on a team that's developing an app that takes song lyrics and audio attributes to predict the song name and artist. It is your responsibility to model the portion of the Machine Learning app that takes in song lyrics and predicts the possible genre the lyrics are in.





To pull additional data from Genius, I used the client ID below.

My client ID is: Client ID *UwF6gSpmaf5DXAkBla0yhAVshgVyn5RUc88UeMfQ_N_y_Mnsly-DRHeNq_4Tm0aR*.

## Data Gathering and Cleaning

This notebook focuses on the data gathering, light cleaning and preprocessing of our lyrics dataset. We will begin with importing the necessary packages and also following steps to get the final csv file that will be used in our final notebook.

In [1]:
import pandas as pd
import regex
import seaborn as sns
import numpy as np
import matplotlib.pyplot as plt
import collections
import csv
%matplotlib inline

import os
import json
import urllib
import requests
import spotipy
import spotipy.util as util
from bs4 import BeautifulSoup
from sklearn.feature_selection import VarianceThreshold

from sklearn.feature_extraction.text import CountVectorizer
from sklearn.model_selection import train_test_split, GridSearchCV, cross_val_score
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import confusion_matrix, classification_report, accuracy_score
from sklearn.pipeline import make_pipeline, Pipeline
from sklearn.preprocessing import StandardScaler
from sklearn.svm import SVC, LinearSVC
from sklearn.ensemble import RandomForestClassifier, AdaBoostClassifier, VotingClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.metrics import plot_confusion_matrix
from sklearn.feature_extraction.text import TfidfVectorizer
from gensim.models import Word2Vec, KeyedVectors
from sklearn.naive_bayes import MultinomialNB


In [2]:
#this datasets came from Kaggle.
tracks = pd.read_csv('./Data/data.csv')

I ended up scrapping two of the datasets cause of redundancy. I am scraping lyrics into a dataset further down below. I will use these lyrics and match them to artists name (by index).

In [3]:
tracks.head(3)


acousticness                    artists  danceability  duration_ms  energy  \
0         0.991            ['Mamie Smith']         0.598       168333   0.224   
1         0.643  ["Screamin' Jay Hawkins"]         0.852       150200   0.517   
2         0.993            ['Mamie Smith']         0.647       163827   0.186   

   explicit                      id  instrumentalness  key  liveness  \
0         0  0cS0A1fUEUd1EW3FcF8AEI          0.000522    5    0.3790   
1         0  0hbkKFIJm7Z05H8Zl9w30f          0.026400    5    0.0809   
2         0  11m7laMUgmOKqI3oYzuhne          0.000018    0    0.5190   

   loudness  mode                      name  popularity release_date  \
0   -12.628     0  Keep A Song In Your Soul          12         1920   
1    -7.261     0      I Put A Spell On You           7   1920-01-05   
2   -12.098     1              Golfing Papa           4         1920   

   speechiness    tempo  valence  year  
0       0.0936  149.976    0.634  1920  
1       0.0534   86.889    0.950  1920  
2       0.1740   97.600    0.689  1920

In [4]:
tracks = tracks.drop(['release_date', 'duration_ms', 'year'], axis=1) #Dropping features that aren't contributing to my data.

In [5]:
print(type(tracks.loc[0, 'artists']))

tracks['artists'] = tracks['artists'].str.strip('[]') #stripping off brackets and extra quotations in the artists column
tracks['artists'] = tracks['artists'].str.strip("''")
tracks['artists'] = tracks['artists'].str.strip('""')
tracks.set_index('artists', inplace=True)

<class 'str'>


In [7]:
print(f'The track shape is {tracks.shape}')

The track shape is (174389, 16)


In [8]:
tracks.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 174389 entries, 0 to 174388
Data columns (total 16 columns):
 #   Column            Non-Null Count   Dtype  
---  ------            --------------   -----  
 0   acousticness      174389 non-null  float64
 1   artists           174389 non-null  object 
 2   danceability      174389 non-null  float64
 3   energy            174389 non-null  float64
 4   explicit          174389 non-null  int64  
 5   id                174389 non-null  object 
 6   instrumentalness  174389 non-null  float64
 7   key               174389 non-null  int64  
 8   liveness          174389 non-null  float64
 9   loudness          174389 non-null  float64
 10  mode              174389 non-null  int64  
 11  name              174389 non-null  object 
 12  popularity        174389 non-null  int64  
 13  speechiness       174389 non-null  float64
 14  tempo             174389 non-null  float64
 15  valence           174389 non-null  float64
dtypes: float64(9), int64

In [8]:
pip install lyricsgenius #This package is being used to help with scraping data from genius.com

In [8]:
import lyricsgenius as lg

In [9]:
genius = lg.Genius('UwF6gSpmaf5DXAkBla0yhAVshgVyn5RUc88UeMfQ_N_y_Mnsly-DRHeNq_4Tm0aR', #This will be used to access the genius API so that lyrics can be scraped.
                   skip_non_songs=True, excluded_terms=["(Remix)", "(Live)"], 
                   remove_section_headers=True)

## Scraping our lyrics from Genius
The function below will be used to scrape our data and append it to a dictionary for each artist.

In [19]:
#A portion of this code was adapted from https://www.johnwmillr.com/

#Once we gain access from the ID above, we will create a function to iterate through artists names.
import csv
lyrics_d = {};


def get_lyrics(arr, d): #this function takes an argument arr for 'artist name', and "d" for amount of song lyrics you want pulled.
    counter = 0
    for name in arr: 
        try:
            songs = (genius.search_artist(name, max_songs=d, sort='popularity')).songs #Songs are sorted by popularity and d is input as a long limit
            s = [song.lyrics for song in songs]
            lyrics_d[name] = s  #This is adding each artist and their lyrics to a dictionary as a key and value.
            
            w = csv.writer(open(r"C:\Users\Fib0nacci\Desktop\lyric_d.csv", "a")) #Saving this to a dictionary on my desktop.
            w.writerow([name, s])
            for key, val in lyrics_d.items():
                w.writerow([key, val]) #Writing each name and song lyric to our file and increasing the count
            counter += 1
                #w.close()
            print(f"Songs grabbed:{len(s)}")
        except:
            print(f"some exception at {name}: {counter}") #This prints an exception in the event a song is not located for an artist.
            


In [14]:
#Creating a df of artist names to use in our function. This will allow me to iterate through each unique artist name.
#This will cut down the time it takes for our function to run.
ind = range(len(tracks_names)) 

df_name = pd.DataFrame(tracks_names.keys(), index = ind)

In [16]:
df_name.columns.values.tolist()
df_name['artists'] = df_name[0]

In [17]:
#renaming the artists column
df_name = df_name.drop([0], axis=1)
df_name.head()

artists
0                    Mamie Smith
1          Screamin' Jay Hawkins
2                Oscar Velazquez
3                           Mixe
4  Mamie Smith & Her Jazz Hounds

In [20]:
artists = df_name['artists'] #Now we have only unique artist names.
artists

0                                 Mamie Smith
1                       Screamin' Jay Hawkins
2                             Oscar Velazquez
3                                        Mixe
4               Mamie Smith & Her Jazz Hounds
                         ...                 
36190                      RAYE', 'Rudimental
36191               Don Omar', 'Kendo Kapponi
36192                Don Omar', 'Mackie Ranks
36193               Sfera Ebbasta', 'J Balvin
36194    Ludovico Einaudi', 'Johannes Bornlöf
Name: artists, Length: 36195, dtype: object

In [21]:
#The artists variable from above was used in the song lyrics function to grab songs from each unique artist.
get_lyrics(artists, 1)

Searching for songs by Mamie Smith...

Song 1: "Crazy Blues"

Reached user-specified song limit (1).
Done. Found 1 songs.
Songs grabbed:1
Searching for songs by Screamin' Jay Hawkins...

Changing artist name to 'Screamin’ Jay Hawkins'
Song 1: "I Put a Spell on You"

Reached user-specified song limit (1).
Done. Found 1 songs.
Songs grabbed:1
Searching for songs by Oscar Velazquez...

Changing artist name to 'Oscar velazquez'
Done. Found 0 songs.
Songs grabbed:0
Searching for songs by Mixe...

Changing artist name to '​mixed matches'
Song 1: "Maybe"

Reached user-specified song limit (1).
Done. Found 1 songs.
Songs grabbed:1
Searching for songs by Mamie Smith & Her Jazz Hounds...

No results found for 'Mamie Smith & Her Jazz Hounds'.
some exception at Mamie Smith & Her Jazz Hounds: 4
Searching for songs by Francisco Canaro...

Song 1: "El adiós"

Reached user-specified song limit (1).
Done. Found 1 songs.
Songs grabbed:1
Searching for songs by Meetya...

Changing artist name to 'MeetAnth

Done. Found 0 songs.
Songs grabbed:0
Searching for songs by Claudia Robine...

No results found for 'Claudia Robine'.
some exception at Claudia Robine: 27
Searching for songs by Athanásios Kanéllis...

No results found for 'Athanásios Kanéllis'.
some exception at Athanásios Kanéllis: 27
Searching for songs by Matthaíos Felónis...

No results found for 'Matthaíos Felónis'.
some exception at Matthaíos Felónis: 27
Searching for songs by Ioannis Xalkias...

No results found for 'Ioannis Xalkias'.
some exception at Ioannis Xalkias: 27
Searching for songs by Xaralampos Kritikos...

No results found for 'Xaralampos Kritikos'.
some exception at Xaralampos Kritikos: 27
Searching for songs by OsamaBeenLeanin...

Song 1: "SideRaq 2019"

Reached user-specified song limit (1).
Done. Found 1 songs.
Songs grabbed:1
Searching for songs by Dréan...

Changing artist name to 'Dreannn M.'
Song 1: "Drop Down"

Reached user-specified song limit (1).
Done. Found 1 songs.
some exception at Dréan: 28
Searching

No results found for 'Sergei Rachmaninoff', 'Yuri Temirkanov', 'St. Petersburg Philharmonic Orchestra'.
some exception at Sergei Rachmaninoff', 'Yuri Temirkanov', 'St. Petersburg Philharmonic Orchestra: 28
Searching for songs by Felix Mendelssohn', 'Arturo Toscanini...

No results found for 'Felix Mendelssohn', 'Arturo Toscanini'.
some exception at Felix Mendelssohn', 'Arturo Toscanini: 28
Searching for songs by Sergei Rachmaninoff', 'Zubin Mehta', 'Vladimir Feltsman', 'Israel Philharmonic Orchestra...

No results found for 'Sergei Rachmaninoff', 'Zubin Mehta', 'Vladimir Feltsman', 'Israel Philharmonic Orchestra'.
some exception at Sergei Rachmaninoff', 'Zubin Mehta', 'Vladimir Feltsman', 'Israel Philharmonic Orchestra: 28
Searching for songs by Morton Downey...

Done. Found 0 songs.
some exception at Morton Downey: 28
Searching for songs by Louis Boucot...

No results found for 'Louis Boucot'.
some exception at Louis Boucot: 28
Searching for songs by Thomas Hallsten Paine...

No resul

Changing artist name to 'Fletcher Henderson and His Orchestra'
Song 1: "It’s The Darndest Thing"

Reached user-specified song limit (1).
Done. Found 1 songs.
some exception at Fletcher Henderson & His Orchestra: 28
Searching for songs by Louis Armstrong & His Sebastian New Cotton Club Orchestra...

Song 1: "Shine"

Reached user-specified song limit (1).
Done. Found 1 songs.
some exception at Louis Armstrong & His Sebastian New Cotton Club Orchestra: 28
Searching for songs by Maggie Jones...

Song 1: "Suicide Blues"

Reached user-specified song limit (1).
Done. Found 1 songs.
some exception at Maggie Jones: 28
Searching for songs by Margaret Johnson...

Done. Found 0 songs.
some exception at Margaret Johnson: 28
Searching for songs by Louis Armstrong & His Hot Seven...

Song 1: "Potato Head Blues"

Reached user-specified song limit (1).
Done. Found 1 songs.
some exception at Louis Armstrong & His Hot Seven: 28
Searching for songs by Bertha "Chippie" Hill', 'Louis Armstrong...

No result

No results found for 'Georges Milton'.
some exception at Georges Milton: 28
Searching for songs by Sara Gee & Ramblin Matt...

No results found for 'Sara Gee & Ramblin Matt'.
some exception at Sara Gee & Ramblin Matt: 28
Searching for songs by Johann Sebastian Bach...

Song 1: "Jesus bleibet meine Freude"

Reached user-specified song limit (1).
Done. Found 1 songs.
some exception at Johann Sebastian Bach: 28
Searching for songs by Bayan Sultan...

No results found for 'Bayan Sultan'.
some exception at Bayan Sultan: 28
Searching for songs by Bix Beiderbecke And His Orchestra', 'Bix Beiderbecke...

Changing artist name to 'Frankie Trumbauer and His Orchestra (featuring Bix Biederbecke)'
Song 1: "Louise (OKeh 41231)"

Reached user-specified song limit (1).
Done. Found 1 songs.
some exception at Bix Beiderbecke And His Orchestra', 'Bix Beiderbecke: 28
Searching for songs by Lionel Hampton Orchestra...

Changing artist name to 'Lionel Hampton And His Orchestra'
Song 1: "It Don’t Mean A Thin

...

some exception at Day Wave: 28
Searching for songs by DeJ Loaf', 'Future...

some exception at DeJ Loaf', 'Future: 28
Searching for songs by Casey Veggies', 'DeJ Loaf...

some exception at Casey Veggies', 'DeJ Loaf: 28
Searching for songs by Lynn Shore', 'Mark Vogel...

some exception at Lynn Shore', 'Mark Vogel: 28
Searching for songs by Beautiful Chorus...

some exception at Beautiful Chorus: 28
Searching for songs by Young Thug', 'Duke...

some exception at Young Thug', 'Duke: 28
Searching for songs by Shovels & Rope', 'Shakey Graves...

some exception at Shovels & Rope', 'Shakey Graves: 28
Searching for songs by EARTHGANG...

some exception at EARTHGANG: 28
Searching for songs by Kuana Torres Kahele', 'Napua Greig', 'James Ford Murphy...

some exception at Kuana Torres Kahele', 'Napua Greig', 'James Ford Murphy: 28
Searching for songs by Matt Simons', 'Falco van den Acker', 'Bob Van Ratingen...

some exception at Matt Simons', 'Falco van den Acker', 'Bob Van Ratingen: 28
Searching 

some exception at Lil Yachty', 'Quavo', 'Skippa Da Flippa', 'Young Thug: 28
Searching for songs by Valiant Coos', 'Luigi Peretti', 'Beni Bonkers...

some exception at Valiant Coos', 'Luigi Peretti', 'Beni Bonkers: 28
Searching for songs by Valiant Coos...

some exception at Valiant Coos: 28
Searching for songs by Fran Denia...

some exception at Fran Denia: 28
Searching for songs by Rodrigo Diaz...

some exception at Rodrigo Diaz: 28
Searching for songs by Kid Bloom...

some exception at Kid Bloom: 28
Searching for songs by Strobetech...

some exception at Strobetech: 28
Searching for songs by Struggle Jennings', 'Aaron Lewis...

some exception at Struggle Jennings', 'Aaron Lewis: 28
Searching for songs by The Lagoons...

some exception at The Lagoons: 28
Searching for songs by DgtalSystem...

some exception at DgtalSystem: 28
Searching for songs by Aerodroemme', 'John Deere...

some exception at Aerodroemme', 'John Deere: 28
Searching for songs by Danny Silberman...

some exception at

some exception at Esthie: 28
Searching for songs by Martin Garrix', 'Troye Sivan...

some exception at Martin Garrix', 'Troye Sivan: 28
Searching for songs by Soulful Piano Group', 'Chakra Balancing Sound Therapy', 'Chillout Lounge Piano...

some exception at Soulful Piano Group', 'Chakra Balancing Sound Therapy', 'Chillout Lounge Piano: 28
Searching for songs by Tyler, The Creator', 'Jaden...

some exception at Tyler, The Creator', 'Jaden: 28
Searching for songs by Grupo Arranke...

some exception at Grupo Arranke: 28
Searching for songs by Clean Bandit', 'Demi Lovato...

some exception at Clean Bandit', 'Demi Lovato: 28
Searching for songs by Maurice West...

some exception at Maurice West: 28
Searching for songs by Lil Baby', 'Gunna', 'Lil Durk', 'NAV...

some exception at Lil Baby', 'Gunna', 'Lil Durk', 'NAV: 28
Searching for songs by ZZanu...

some exception at ZZanu: 28
Searching for songs by Bogdan Vix', 'KeyPlayer', 'Moua...

some exception at Bogdan Vix', 'KeyPlayer', 'Moua: 2

some exception at p4rkr: 28
Searching for songs by WNX...

some exception at WNX: 28
Searching for songs by Alan Walker', 'Sabrina Carpenter', 'Farruko...

some exception at Alan Walker', 'Sabrina Carpenter', 'Farruko: 28
Searching for songs by Ibiza Chill Lounge...

some exception at Ibiza Chill Lounge: 28
Searching for songs by Secretto...

some exception at Secretto: 28
Searching for songs by Mark Sixma', 'T99...

some exception at Mark Sixma', 'T99: 28
Searching for songs by Kialph...

some exception at Kialph: 28
Searching for songs by Ty Dolla $ign', 'J. Cole...

some exception at Ty Dolla $ign', 'J. Cole: 28
Searching for songs by La Fete...

some exception at La Fete: 28
Searching for songs by DaniLeigh', 'G-Eazy...

some exception at DaniLeigh', 'G-Eazy: 28
Searching for songs by Saint Tropez Radio Lounge Chillout Music Club...

some exception at Saint Tropez Radio Lounge Chillout Music Club: 28
Searching for songs by Gabrielle Aplin', 'JP Cooper...

some exception at Gabriell

some exception at Drego: 28
Searching for songs by Jeris Johnson', 'Ricky Desktop...

some exception at Jeris Johnson', 'Ricky Desktop: 28
Searching for songs by Kewlie...

some exception at Kewlie: 28
Searching for songs by coastal...

some exception at coastal: 28
Searching for songs by Cali Soul', 'golden era', 'Ol Wallace...

some exception at Cali Soul', 'golden era', 'Ol Wallace: 28
Searching for songs by Ty Dolla $ign', 'Jhené Aiko', 'Mustard...

some exception at Ty Dolla $ign', 'Jhené Aiko', 'Mustard: 28
Searching for songs by Dasha Rush...

some exception at Dasha Rush: 28
Searching for songs by $NOT', 'Wifisfuneral...

some exception at $NOT', 'Wifisfuneral: 28
Searching for songs by Lil Durk', 'YNW Melly...

some exception at Lil Durk', 'YNW Melly: 28
Searching for songs by Jordan Young...

some exception at Jordan Young: 28
Searching for songs by R3HAB', 'Andy Grammer...

some exception at R3HAB', 'Andy Grammer: 28
Searching for songs by Kat & Alex...

some exception at Ka

In [1]:
lyrics_d.keys() #Taking a look at our new dictionary keys.

In [44]:
with open('songs.csv', 'w', encoding="utf-8") as csvfile: #We are writing our dictionary to a csv file for easy loading.
    writer = csv.DictWriter(csvfile, lyrics_d.keys())
    writer.writeheader()
    writer.writerow(lyrics_d)

In [88]:
song_lyric = pd.read_csv('./songs.csv')
song_lyric.head()

Mamie Smith  \
0  ["I can't sleep at night\nI can't eat a bite\n...   

                               Screamin' Jay Hawkins Oscar Velazquez  \
0  ["I put a spell on you\nBecause you're mine\nS...              []   

                                                Mixe  \
0  ["Just take\nJust take it\nWith how you want t...   

                                    Francisco Canaro  \
0  ['¡Adiós pampa mía!...\nMe voy... Me voy a tie...   

                                              Meetya Dorville  \
0  ["Come on in!  If your with me\n\nThere is a w...       []   

                                            Justrock  \
0  ['She won’t like dubstep\nShe likes electro\nS...   

                                               Tr0ma  \
0  ['(Yeah) Kane is in the building, nigga\nIt\'s...   

                                              Jodoli  ...  \
0  ["I like me best when my heads on your shoulde...  ...   

                                         Dirty Looks  \
0  ['Baby is good, baby\'s understood\nBaby is do...   

                                      Tisha Campbell  \
0  ["It's the journey...\nUp and down like a roll...   

                                        Frank Morgan  \
0  ["Skylark\nHave you anything to say to me?\nWo...   

                                        Bert Dominic  \
0  ['Bass, bass, bass\nO.o sick basS o.O\nFeel th...   

                                       Dave Valentin  \
0  ["It's early in the morning and I'm feeling ki...   

                                                1927  \
0  ["If I could paint\nI'd paint a portrait of yo...   

                                               Sadus  \
0  ["Loss of vision\nBrain contusion\nSight and s...   

                                        Danielle Dax  \
0  ["Up in the Big House\nThey're branding nigger...   

                                    David Arkenstone  \
0  ["Lullaby\nLullaby\nLay down your head and I'l...   

                                                Kult  
0  ['Mój dom murem podzielony\nPodzielone murem s...  

[1 rows x 9054 columns]

In [89]:
new = pd.DataFrame.from_dict(lyrics_d, orient ='index') #Now we will create a datafram out of our song_lyrics data.
new.to_csv('song_lyrics.csv', index = True)
new.head()

0
Mamie Smith            I can't sleep at night\nI can't eat a bite\n'C...
Screamin' Jay Hawkins  I put a spell on you\nBecause you're mine\nSto...
Oscar Velazquez                                                     None
Mixe                   Just take\nJust take it\nWith how you want to ...
Francisco Canaro       ¡Adiós pampa mía!...\nMe voy... Me voy a tierr...

In [90]:
new['lyrics'] = new[0]
new = new.drop([0], axis=1)
new.shape

(9054, 1)

In [91]:
#We will reset the index and change the name of the dataframe features.
new.reset_index(level=0, inplace=True)
#new = new.drop('index', axis=1)
new.rename(columns={'index': 'artists'}, inplace=True)

In [93]:
#new = new.drop('level_0', axis=1)
new.head()

artists                                             lyrics
0            Mamie Smith  I can't sleep at night\nI can't eat a bite\n'C...
1  Screamin' Jay Hawkins  I put a spell on you\nBecause you're mine\nSto...
2        Oscar Velazquez                                               None
3                   Mixe  Just take\nJust take it\nWith how you want to ...
4       Francisco Canaro  ¡Adiós pampa mía!...\nMe voy... Me voy a tierr...

In [181]:
#Now, we will merge the 2 dataframes together to create a new one. This will merge based on artist name.
tracks_new = tracks.merge(new, left_on='artists', right_on='artists', how='left')
tracks_new.to_csv('tracks_new.csv', index = True)

In [99]:
tracks_new.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 174389 entries, 0 to 174388
Data columns (total 17 columns):
 #   Column            Non-Null Count   Dtype  
---  ------            --------------   -----  
 0   acousticness      174389 non-null  float64
 1   artists           174389 non-null  object 
 2   danceability      174389 non-null  float64
 3   energy            174389 non-null  float64
 4   explicit          174389 non-null  int64  
 5   id                174389 non-null  object 
 6   instrumentalness  174389 non-null  float64
 7   key               174389 non-null  int64  
 8   liveness          174389 non-null  float64
 9   loudness          174389 non-null  float64
 10  mode              174389 non-null  int64  
 11  name              174389 non-null  object 
 12  popularity        174389 non-null  int64  
 13  speechiness       174389 non-null  float64
 14  tempo             174389 non-null  float64
 15  valence           174389 non-null  float64
 16  lyrics            74

In [105]:
#We have gathered more lyrics data from Kaggle and we will load it and clean it up.
#There are many null values.. we will drop these to explore whether or not to keep them.
more_1 = pd.read_csv('./data/lyrics-data.csv')
more_1.head(3)

ALink              SName                                  SLink  \
0  /10000-maniacs/     More Than This     /10000-maniacs/more-than-this.html   
1  /10000-maniacs/  Because The Night  /10000-maniacs/because-the-night.html   
2  /10000-maniacs/     These Are Days     /10000-maniacs/these-are-days.html   

                                               Lyric    Idiom  
0  I could feel at the time. There was no way of ...  ENGLISH  
1  Take me now, baby, here as I am. Hold me close...  ENGLISH  
2  These are. These are days you'll remember. Nev...  ENGLISH

In [3]:
#Renaming the column "Alink" to merge with more_2 df.
more_1.rename(columns={'ALink': 'Link'}, inplace=True)

In [126]:
more_2 = pd.read_csv('./data/artists-data.csv')
more_2.head(3)

Artist  Songs  Popularity             Link Genre  \
0  10000 Maniacs    110         0.3  /10000-maniacs/  Rock   
1      12 Stones     75         0.3      /12-stones/  Rock   
2            311    196         0.5            /311/  Rock   

                                              Genres  
0  Rock; Pop; Electronica; Dance; J-Pop/J-Rock; G...  
1  Rock; Gospel/Religioso; Hard Rock; Grunge; Roc...  
2  Rock; Surf Music; Reggae; Ska; Pop/Rock; Rock ...

In [127]:
more_2.rename(columns={'Artist': 'artists'}, inplace=True)
more_2.shape

(3242, 6)

In [128]:
merged_more = more_1.merge(more_2, left_on='Link', right_on='Link', how='left')  #Here we are merging based on the link data.

In [157]:
merged_more = pd.DataFrame(merged_more)

In [162]:
merged_more.head()

Link              SName                                  SLink  \
0  /10000-maniacs/     More Than This     /10000-maniacs/more-than-this.html   
1  /10000-maniacs/     More Than This     /10000-maniacs/more-than-this.html   
2  /10000-maniacs/  Because The Night  /10000-maniacs/because-the-night.html   
3  /10000-maniacs/  Because The Night  /10000-maniacs/because-the-night.html   
4  /10000-maniacs/     These Are Days     /10000-maniacs/these-are-days.html   

                                               Lyric    Idiom        artists  \
0  I could feel at the time. There was no way of ...  ENGLISH  10000 Maniacs   
1  I could feel at the time. There was no way of ...  ENGLISH  10000 Maniacs   
2  Take me now, baby, here as I am. Hold me close...  ENGLISH  10000 Maniacs   
3  Take me now, baby, here as I am. Hold me close...  ENGLISH  10000 Maniacs   
4  These are. These are days you'll remember. Nev...  ENGLISH  10000 Maniacs   

   Songs  Popularity Genre                                             Genres  
0  110.0         0.3  Rock  Rock; Pop; Electronica; Dance; J-Pop/J-Rock; G...  
1  110.0         0.3   Pop  Rock; Pop; Electronica; Dance; J-Pop/J-Rock; G...  
2  110.0         0.3  Rock  Rock; Pop; Electronica; Dance; J-Pop/J-Rock; G...  
3  110.0         0.3   Pop  Rock; Pop; Electronica; Dance; J-Pop/J-Rock; G...  
4  110.0         0.3  Rock  Rock; Pop; Electronica; Dance; J-Pop/J-Rock; G...

In [131]:
merged_more.shape #Viewing the shape and dropping all duplicate rows.

(234939, 10)

In [132]:
merged_more['SName'].nunique() #There's duplicates, so I will drop them.

128083

In [133]:
merged = merged_more.drop_duplicates(subset=['SName'])

In [4]:
display(merged.shape)

In [135]:
merged = merged.drop(['Link', 'SLink', 'Idiom', 'Songs', 'Popularity', 'Genres'], axis=1)
merged.head(3) #We will also be dropping columns that are not significant for our dataset.

SName                                              Lyric  \
0     More Than This  I could feel at the time. There was no way of ...   
2  Because The Night  Take me now, baby, here as I am. Hold me close...   
4     These Are Days  These are. These are days you'll remember. Nev...   

         artists Genre  
0  10000 Maniacs  Rock  
2  10000 Maniacs  Rock  
4  10000 Maniacs  Rock

In [179]:
#renaming the columns
merged.rename(columns={'SName': 'name'}, inplace=True)
merged.rename(columns={'Lyric': 'lyrics'}, inplace=True)

In [177]:
merged= merged.dropna() #No more null values here!
merged.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 123362 entries, 0 to 234938
Data columns (total 4 columns):
 #   Column   Non-Null Count   Dtype 
---  ------   --------------   ----- 
 0   name     123362 non-null  object
 1   lyrics   123362 non-null  object
 2   artists  123362 non-null  object
 3   Genre    123362 non-null  object
dtypes: object(4)
memory usage: 4.7+ MB


Now we will merge the dataframes based on the artists and their lyrics. We are doing this to clean up the dataset, as our original dataframe mapped lyrics to each artist, regardless of song name. We can the correct songs to go with the correct lyrics, so this is how we will solve the issue.

In [214]:
tracks_new['lyrics_tot']= tracks_new['lyrics'].mask(pd.isnull, merged['lyrics'])

tracks_new['new_lyrics'] = tracks_new['name'].map(merged.set_index('name')['lyrics'])

tracks_new['lyrics_correct'] = tracks_new['new_lyrics'].fillna(tracks_new['lyrics_tot'])

tracks_new = tracks_new.drop(['lyrics', 'lyrics_tot'], axis=1)

In [216]:
 tracks_new = tracks_new.drop(['new_lyrics'], axis=1)

In [217]:
tracks_new.info() #Checking the info again to see how many and where are nan values are.

<class 'pandas.core.frame.DataFrame'>
Int64Index: 174389 entries, 0 to 174388
Data columns (total 17 columns):
 #   Column            Non-Null Count   Dtype  
---  ------            --------------   -----  
 0   acousticness      174389 non-null  float64
 1   artists           174389 non-null  object 
 2   danceability      174389 non-null  float64
 3   energy            174389 non-null  float64
 4   explicit          174389 non-null  int64  
 5   id                174389 non-null  object 
 6   instrumentalness  174389 non-null  float64
 7   key               174389 non-null  int64  
 8   liveness          174389 non-null  float64
 9   loudness          174389 non-null  float64
 10  mode              174389 non-null  int64  
 11  name              174389 non-null  object 
 12  popularity        174389 non-null  int64  
 13  speechiness       174389 non-null  float64
 14  tempo             174389 non-null  float64
 15  valence           174389 non-null  float64
 16  lyrics_correct    91

In [5]:
#After merging another dataframe, I was finally able to drop the Nan values.
tracks_new = tracks_new.dropna()

In [ ]:
tracks_new.to_csv('tracks_final.csv', index = True) #Saving our newly merged dataframe.

tracks_f = pd.read_csv('./tracks_final.csv') #reloading it to confirm it saved correctly.

In [3]:
#Now I will strip the tracks down to just the lyrics. Since this is what we want to train our model on, I will only be focusing on components
#not necessarily contributed to audio features.
tracks_f = tracks_f.drop(['speechiness', 'valence', 'tempo', 'mode', 'loudness', 'liveness', 'key', 'instrumentalness',
                         'id', 'explicit', 'danceability', 'energy', 'acousticness', 'Unnamed: 0'], axis=1)
tracks_f.to_csv('./tracks_f.csv', index = True)

In [4]:
tracks_f.head()

artists                          name  popularity  \
0            Mamie Smith      Keep A Song In Your Soul          12   
1  Screamin' Jay Hawkins          I Put A Spell On You           7   
2            Mamie Smith                  Golfing Papa           4   
3                   Mixe                     Xuniverxe           2   
4            Mamie Smith  Don't You Advertise Your Man           5   

                                      lyrics_correct  
0  I can't sleep at night\nI can't eat a bite\n'C...  
1  I put a spell on you. Because you're mine.. Yo...  
2  I can't sleep at night\nI can't eat a bite\n'C...  
3  Just take\nJust take it\nWith how you want to ...  
4  I can't sleep at night\nI can't eat a bite\n'C...

In [5]:
#Cleaning up the lyrics.
#This function uses nltk, lemmatizing, tokenizing and stop words to clean the strings in our dataset.

import string
import re
import nltk
from nltk.stem import WordNetLemmatizer
from nltk.stem.porter import PorterStemmer
from nltk.tokenize import word_tokenize, RegexpTokenizer
from nltk.corpus import stopwords

nltk.download('stopwords')
nltk.download('wordnet')
stop_words = nltk.corpus.stopwords.words('english') #Placed outside of the function for word appendage.

lem = WordNetLemmatizer() #lemmitization brings context to words, similar to stemming

#This function cleans the series data.
def cleanup(unique_post):
    #removes special characters and only leaves upper and lower case letters
    just_letters = re.sub('[^a-zA-Z]', 
                          ' ', 
                          str(unique_post)
                         )
    
    #lowercasing all letters
    words = just_letters.lower().split()

    #converting stop words and removing them.
    stop = set(stop_words)

    #Now combine lemmatizing and removal of stop words to get just words and their lem versions.
    #I am using lemmatization over stemming because many lyrics have related words forms. (lexical knowledge base)

    #true_words = [lem.lemmatize(word) for word in words if word not in stop] for 
    true_words = [word for word in words if word not in stop]

    return(' '.join(true_words))


[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Fib0nacci\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\Fib0nacci\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [6]:
tracks_f['lyrics_cleaned'] = tracks_f['lyrics_correct'].map(cleanup)

In [7]:
tracks_f['lyrics_correct'] = tracks_f['lyrics_correct'].map(cleanup)

In [8]:
tracks_f.head(5) #our cleaned lyrics dataset

artists                          name  popularity  \
0            Mamie Smith      Keep A Song In Your Soul          12   
1  Screamin' Jay Hawkins          I Put A Spell On You           7   
2            Mamie Smith                  Golfing Papa           4   
3                   Mixe                     Xuniverxe           2   
4            Mamie Smith  Don't You Advertise Your Man           5   

                                      lyrics_correct  \
0  sleep night eat bite cause man love treat righ...   
1  put spell mine better stop things doin said wa...   
2  sleep night eat bite cause man love treat righ...   
3  take take want live subtle moment want begin t...   
4  sleep night eat bite cause man love treat righ...   

                                      lyrics_cleaned  
0  sleep night eat bite cause man love treat righ...  
1  put spell mine better stop things doin said wa...  
2  sleep night eat bite cause man love treat righ...  
3  take take want live subtle moment want begin t...  
4  sleep night eat bite cause man love treat righ...

Now we will read in our genres dataset and work on merging that with our tracks_f.

In [6]:
genres = pd.read_csv(r'C:\Users\Fib0nacci\Desktop\data\audio_feats.csv') #reading in our cleaned genres dataset from our audio features.
genres.head(1)

Unnamed: 0  acousticness      artists  danceability  duration_ms  energy  \
0           0         0.991  Mamie Smith         0.598       168333   0.224   

   explicit  instrumentalness  key  liveness  loudness  mode  \
0         0          0.000522    5     0.379   -12.628     0   

                       name  popularity  speechiness    tempo  valence  \
0  Keep A Song In Your Soul          12       0.0936  149.976    0.634   

  new_genres  
0      blues

In [13]:
lyrics = genres.merge(tracks_f, left_on='name', right_on='name', how='left')

In [7]:
#now, I will merge this dataset with the genres category of the other dataset.
lyrics = tracks_f.merge(genres, left_on='artists', right_on='artists', how = 'left')

In [16]:
lyrics = lyrics.drop_duplicates(subset=['Unnamed: 0']) #Dropping all duplicate values in the index from column "Unnamed".
lyrics.shape

(137429, 22)

In [7]:
#Dropping more redundant values once the dataframe has been merged.
lyrics = lyrics.drop(['artists_y', 'popularity_y', 'speechiness', 'valence', 'tempo', 'mode', 'loudness', 'liveness', 'key', 'instrumentalness','explicit', 
                      'danceability', 'energy', 'acousticness', 'Unnamed: 0'], axis=1)


In [18]:
lyrics = lyrics.dropna() #Dropping nan values

lyrics = lyrics.drop_duplicates() #Dropping duplicate rows

In [20]:
#Lets further tokenize the dataset to see each individual word in the lyrics
lyrics['lyrics_cleaned'] = lyrics['lyrics_cleaned'].apply(lambda x: word_tokenize(x))


In [21]:
lyrics.head(3)

artists_x  duration_ms                      name  popularity_x  \
0            Mamie Smith       168333  Keep A Song In Your Soul            12   
1  Screamin' Jay Hawkins       150200      I Put A Spell On You             7   
7            Mamie Smith       163827              Golfing Papa             4   

  new_genres                                     lyrics_correct  \
0      blues  sleep night eat bite cause man love treat righ...   
1      blues  put spell mine better stop things doin said wa...   
7      blues  sleep night eat bite cause man love treat righ...   

                                      lyrics_cleaned  
0  [sleep, night, eat, bite, cause, man, love, tr...  
1  [put, spell, mine, better, stop, things, doin,...  
7  [sleep, night, eat, bite, cause, man, love, tr...

In [22]:
lyrics = lyrics.drop(['duration_ms'], axis= 1) #Dropping columns I no longer need

lyrics.rename(columns={'artists_x': 'artists', 'new_genres' : 'genres', 'lyrics_correct': 'lyrics', 'popularity_x' : 'popularity'}, inplace=True)

In [24]:
lyrics = lyrics[[c for c in lyrics if c not in ['genres']] #Moving our genres column to the end of our dataframe.
       + ['genres']]

In [25]:
lyrics = lyrics.reset_index(drop=True) #
lyrics.to_csv('./data/clean_lyrics.csv')

## EDA of Our Audio Attributes

Below, I will be looking at the audio attributes of artists and their songs. TO view more EDA on these attributes, please refer to the Audio_Data_Modeling Notebook. This will give me insight to how these genres are determined by viewing the mean values of each attibute. I will be focusing on the mean value.


In [7]:
#I've changed the artist name to be the index, so that I can get a better sense of what type of music
#has certain dancability levels along with their usual classified genres
tracks.loc['Francisco Canaro'].describe()

acousticness  danceability      energy  explicit  instrumentalness  \
count    951.000000    951.000000  951.000000     951.0        951.000000   
mean       0.987196      0.666187    0.275842       0.0          0.656561   
std        0.022539      0.154529    0.127881       0.0          0.327390   
min        0.553000      0.000000    0.024800       0.0          0.000000   
25%        0.989000      0.564500    0.184000       0.0          0.398000   
50%        0.994000      0.698000    0.256000       0.0          0.822000   
75%        0.995000      0.790000    0.340500       0.0          0.912500   
max        0.996000      0.919000    0.843000       0.0          0.992000   

              key    liveness    loudness        mode  popularity  \
count  951.000000  951.000000  951.000000  951.000000   951.00000   
mean     5.432177    0.193199  -12.824800    0.682440     0.04837   
std      3.326350    0.124497    4.289484    0.465772     0.80379   
min      0.000000    0.030600  -30.398000    0.000000     0.00000   
25%      2.000000    0.112000  -15.482500    0.000000     0.00000   
50%      5.000000    0.140000  -12.851000    1.000000     0.00000   
75%      9.000000    0.236000   -9.751000    1.000000     0.00000   
max     11.000000    0.914000   -3.778000    1.000000    24.00000   

       speechiness       tempo     valence  
count   951.000000  951.000000  951.000000  
mean      0.108203  121.196898    0.737375  
std       0.079450   24.307312    0.157257  
min       0.000000    0.000000    0.000000  
25%       0.058400  114.107500    0.641500  
50%       0.080600  118.108000    0.756000  
75%       0.129500  123.489500    0.858000  
max       0.859000  220.192000    0.974000

### Francisco Canaro Stats
We can see that this artist, who is prominent in tango, has high acoustic mean value, instrumentalness, valence and danceability.

In [8]:
tracks.loc['Busta Rhymes'].describe()

acousticness  danceability     energy   explicit  instrumentalness  \
count     10.000000     10.000000  10.000000  10.000000         10.000000   
mean       0.079286      0.747800   0.716300   0.900000          0.000203   
std        0.134092      0.130309   0.141809   0.316228          0.000546   
min        0.004300      0.562000   0.551000   0.000000          0.000000   
25%        0.008880      0.653500   0.585750   1.000000          0.000000   
50%        0.015450      0.749500   0.716000   1.000000          0.000002   
75%        0.096650      0.862750   0.826000   1.000000          0.000093   
max        0.443000      0.913000   0.924000   1.000000          0.001750   

             key   liveness  loudness       mode  popularity  speechiness  \
count  10.000000  10.000000  10.00000  10.000000   10.000000    10.000000   
mean    5.700000   0.240750  -7.20220   0.200000   48.700000     0.329700   
std     4.643993   0.213610   0.89018   0.421637   12.018966     0.073618   
min     1.000000   0.061300  -8.44600   0.000000   35.000000     0.202000   
25%     1.000000   0.086175  -7.65300   0.000000   38.500000     0.286500   
50%     5.000000   0.179500  -7.22400   0.000000   47.500000     0.331500   
75%    10.750000   0.301500  -6.72300   0.000000   57.750000     0.379750   
max    11.000000   0.771000  -5.43300   1.000000   69.000000     0.450000   

            tempo    valence  
count   10.000000  10.000000  
mean   110.587100   0.691000  
std     30.857027   0.132863  
min     83.011000   0.442000  
25%     88.977000   0.627750  
50%     99.472500   0.726000  
75%    128.367500   0.776000  
max    178.686000   0.878000

###  Busta Rhymes Stats
Here, we see that this artist who is prominent in hip hop, has low acosutic mean, instrumentalness and a lower valence.
However, he has a high explicity, energy, popularity and danceability

In [9]:
tracks.loc['Joey Bada$$'].describe()  


acousticness  danceability    energy  explicit  instrumentalness  \
count      7.000000      7.000000  7.000000       7.0          7.000000   
mean       0.284057      0.679571  0.761857       1.0          0.065046   
std        0.153449      0.140454  0.131341       0.0          0.171953   
min        0.063400      0.451000  0.628000       1.0          0.000000   
25%        0.198500      0.588500  0.657000       1.0          0.000000   
50%        0.262000      0.733000  0.707000       1.0          0.000000   
75%        0.368000      0.792000  0.870500       1.0          0.000162   
max        0.530000      0.812000  0.943000       1.0          0.455000   

             key  liveness  loudness      mode  popularity  speechiness  \
count   7.000000  7.000000  7.000000  7.000000    7.000000     7.000000   
mean    5.571429  0.453714 -4.739571  0.142857   63.000000     0.210314   
std     4.353433  0.270065  1.881996  0.377964    8.445906     0.080098   
min     1.000000  0.151000 -7.088000  0.000000   54.000000     0.068200   
25%     1.000000  0.230000 -5.905000  0.000000   55.500000     0.171500   
50%     8.000000  0.453000 -5.339000  0.000000   62.000000     0.223000   
75%     9.000000  0.619000 -3.671000  0.000000   69.500000     0.276500   
max    10.000000  0.874000 -1.598000  1.000000   75.000000     0.285000   

           tempo   valence  
count    7.00000  7.000000  
mean    96.60200  0.660143  
std     13.89369  0.196870  
min     79.39400  0.452000  
25%     90.16200  0.491000  
50%     93.62000  0.608000  
75%     99.93600  0.834000  
max    123.00400  0.911000

### Joey Badass Stats
Here is another documented hip hop artist. He has high danceability, high energy, high explicity, low acoustics, low instrumentalness in his stats.He also reflects a high popularity, similar to the artist *Busta Rhymes*. These values compared to other hip hop artists help us infer that this artist is more than likely hiphop.

In [6]:
tracks.loc['Phil Collins'].describe()

acousticness  danceability     energy  explicit  instrumentalness  \
count     95.000000     95.000000  95.000000      95.0         95.000000   
mean       0.318985      0.581137   0.620396       0.0          0.048613   
std        0.278001      0.132594   0.260909       0.0          0.169851   
min        0.000987      0.205000   0.073800       0.0          0.000000   
25%        0.074800      0.519000   0.401000       0.0          0.000081   
50%        0.212000      0.610000   0.699000       0.0          0.001050   
75%        0.502500      0.659000   0.851500       0.0          0.007650   
max        0.914000      0.807000   0.987000       0.0          0.957000   

            key   liveness   loudness       mode  popularity  speechiness  \
count  95.00000  95.000000  95.000000  95.000000   95.000000    95.000000   
mean    4.80000   0.215489  -8.552863   0.705263   44.368421     0.041268   
std     3.02683   0.272594   3.340261   0.458343   12.467023     0.016965   
min     0.00000   0.032800 -17.347000   0.000000   26.000000     0.024200   
25%     3.00000   0.072900 -10.234000   0.000000   34.500000     0.030600   
50%     5.00000   0.098900  -8.201000   1.000000   43.000000     0.037000   
75%     7.50000   0.219500  -5.935000   1.000000   50.000000     0.043250   
max    11.00000   0.988000  -2.939000   1.000000   77.000000     0.100000   

            tempo    valence  
count   95.000000  95.000000  
mean   120.891105   0.478663  
std     25.935902   0.231482  
min     58.991000   0.060100  
25%    101.976000   0.314500  
50%    118.796000   0.443000  
75%    136.393500   0.663000  
max    189.999000   0.952000

# Phil Collins Stats
Phill Collins is classified as "pop" generally speaking. His stats show that his music has a high popularity along with a high tempo and energy. The danceability of his music is also high, but the speechiness is low, so we can see that this would not fit into the "hip hop" genre if we compare it to the hip hop artists above.